![Urgences - Image CC0 - pexels.com](img/pexels-pixabay-263402.jpg "Urgences")

# Challenge - [ED Lab Prediction]
_Nom à trouver_

Ce notebook est à destination de l'équipe travaillant autours du projet.  
L'objectif est de présenter sommairement le projet et les données.

# Rationel

_@TODO Levi_

# Données

Les données sont issus du projet MIMIC-IV.  
Le projet MIMIC est un projet d'open-data médical initié par l'hopital _Beth Israel Deaconess_ à Boston.  
Initialement, seul des données de réanimation été accessible.

Pour sa 4ème édition, a été mis à disposition un jeu de données couvrant un spectre bien plus large :
- Données relatives aux passages aux urgences
- Données relatives aux hospitalisations
- Données relatives aux séjour en réanimation
- Données de radiographie thoracique avec compte rendu associé

L'ensemble de ces données ont été mis à disposition dans le cadre de projets complémentaires :
- [MIMIC-IV](https://physionet.org/content/mimiciv/0.4/) : hospitalisation et réanimation
- [MIMIC-IV-ED](https://physionet.org/content/mimic-iv-ed/1.0/) : urgences
- [MIMIC-IV-CXR](https://physionet.org/content/mimic-cxr/2.0.0/) : radiographie thoracique

Ces bases sont complémentaires dans le sens où chaque collecte a été faite durant une période temporelle spécifique, qui se recoupe plus où moins.  
Certains éléments nécessaires à l'exploitation de MIMIC-IV-ED sont présent dans MIMIC-IV.  
La lecture de la documentation de MIMIC-IV et de MIMIC-IV-ED est vivement recommandé (lien ci-dessus).

En complément, un certains nombre de ressources est disponible sur le site du projet [MIMIC-IV](https://mimic.mit.edu/).

Nous proposons de travailler autours de ce jeu de données avec pour objectif la tache suivante : **prédire les examens biologiques qui seront réalisés lors de l'arrivé d'un patient aux urgences**

## Téléchargement des données

La base de données de biologie étant volumineuse (nous y reviendrons plus bas), un pré-traitement des données a été effectué.  
Le pré-traitement est le suivant :
- Intégration de l'ensemble des données utiles au sein d'une base de données SQLITE
- Tri des lignes de biologies afin de ne conserver que celles répondant au critères suivants :
  - Date de réalisation >= date de début du passage aux urgences
  - Date de réalisation <= date de fin du passage aux urgences

Un token de téléchargement des données vous a normallement été mis à disposition.

```
    python3 download_data.py [TOKEN]
```

Le script de transformation est disponible dans `database_constitution/database_constitution.py`.

## Chargement et exploration des données

Les données sont téléchargés dans le dossier data.  
Il est facile de requêter une base sqlite à l'aide de pandas.

In [2]:
import pandas as pd
import sqlite3

In [6]:
# D'abord, il fait établir une connection avec la base
conn = sqlite3.connect("./data/mimic-iv.sqlite")

# Ensuite, on effectue des requête à l'aide de la fonction read_sql de pandas, pour récupérer tous les éléments de la table, il suffit de faire un SELECT * FROM nom_de_la_table
triage = pd.read_sql("SELECT * FROM triage", conn)
triage

index  subject_id   stay_id  temperature  heartrate  resprate  o2sat  \
0            0    15585360  37573921         97.0       87.0      18.0  100.0   
1            1    17192424  34160628         98.6       82.0       NaN  100.0   
2            2    15248757  32172727         97.1      112.0      20.0  100.0   
3            3    16648037  38946064         98.5       59.0      18.0   99.0   
4            4    13492931  39828574        100.6       90.0      16.0   96.0   
...        ...         ...       ...          ...        ...       ...    ...   
448967  448967    17192157  31192693          NaN        NaN       NaN    NaN   
448968  448968    15632852  37860864         98.2      115.0      18.0  100.0   
448969  448969    17526143  30744048          NaN        NaN       NaN    NaN   
448970  448970    18321345  37024607          NaN        NaN       NaN    NaN   
448971  448971    11894181  39631961          NaN        NaN       NaN    NaN   

          sbp   dbp  pain  acuity chiefcomplaint  
0       150.0  71.0  10.0     3.0              
1       111.0  81.0   3.0     3.0                
2       147.0  97.0   8.0     4.0               
3       160.0  86.0   2.0     2.0                
4       107.0  55.0   0.0     3.0              '  
...       ...   ...   ...     ...            ...  
448967    NaN   NaN   NaN     NaN           None  
448968  124.0  68.0   0.0     3.0           None  
448969    NaN   NaN   NaN     2.0           None  
448970    NaN   NaN   NaN     NaN           None  
448971    NaN   NaN   NaN     1.0           None  

[448972 rows x 12 columns]

L'avantage de travailler avec une base sqlite, c'est qu'il nous permet de manipuler et transformer des données qui ne peuvent pas toujours tenir en mémoire vive.  
Quelques exemples de traitements :

In [41]:
# Sélectionner un nombre limité de lignes
labevents_100 = pd.read_sql("SELECT * FROM labevents LIMIT 100", conn)
print("Dimension de labevents_100 : ", labevents_100.shape)

# Compter le nombre de ligne
labevents_n = pd.read_sql("SELECT COUNT(0) FROM labevents", conn)
print("Nombre de lignes dans labevents :", labevents_n.values[0][0])

# Filter des données
labevents_10000764 = pd.read_sql("SELECT * FROM labevents WHERE subject_id = 10000764", conn)
print("Contenu de labevents pour le patient n°10000764 :", labevents_10000764.shape)

Dimension de labevents_100 :  (100, 17)
Nombre de lignes dans labevents : 11594360
Contenu de labevents pour le patient n°10000764 : (27, 17)


Grâce à un système d'index, les transformations de données via sqlite se font relativement rapidement.  
C'est notamment le cas pour les filtre (WHERE) et les jointure.
Un exemple de jointure :

In [44]:
# On récupère le libellé des examens
labevents_with_item = pd.read_sql("""
    SELECT * 
    FROM labevents as le
    LEFT JOIN d_labitems as li
        ON le.itemid = li.itemid
    LIMIT 1000
""", conn)
# Tous les types de jointures : LEFT, RIGHT, INNER, OUTER sont possible

# L'object retourné est toujours un pandas dataframe sur lequel on peux faire les transformations habituelles
labevents_with_item.head(10)

index  labevent_id  subject_id  hadm_id  specimen_id itemid  \
0     0         2599    10000764      NaN     76601642  50971   
1     1         2578    10000764      NaN      6228584  51146   
2     2         2579    10000764      NaN      6228584  51200   
3     3         2580    10000764      NaN      6228584  51221   
4     4         2581    10000764      NaN      6228584  51222   
5     5         2582    10000764      NaN      6228584  51244   
6     6         2583    10000764      NaN      6228584  51248   
7     7         2584    10000764      NaN      6228584  51249   
8     8         2585    10000764      NaN      6228584  51250   
9     9         2586    10000764      NaN      6228584  51254   

             charttime            storetime value  valuenum  ...      flag  \
0  2132-10-14 20:15:00  2132-10-14 21:04:00   4.1       4.1  ...      None   
1  2132-10-14 20:15:00  2132-10-14 20:33:00   0.1       0.1  ...      None   
2  2132-10-14 20:15:00  2132-10-14 20:33:00   0.3       0.3  ...      None   
3  2132-10-14 20:15:00  2132-10-14 20:33:00  40.2      40.2  ...      None   
4  2132-10-14 20:15:00  2132-10-14 20:33:00  14.1      14.1  ...      None   
5  2132-10-14 20:15:00  2132-10-14 20:33:00   4.7       4.7  ...  abnormal   
6  2132-10-14 20:15:00  2132-10-14 20:33:00  32.8      32.8  ...  abnormal   
7  2132-10-14 20:15:00  2132-10-14 20:33:00  35.1      35.1  ...  abnormal   
8  2132-10-14 20:15:00  2132-10-14 20:33:00    93      93.0  ...      None   
9  2132-10-14 20:15:00  2132-10-14 20:33:00   3.8       3.8  ...      None   

   priority  comments   stay_id index itemid        label  fluid    category  \
0      STAT      None  35420907  1236  50971    Potassium  Blood   Chemistry   
1      STAT      None  35420907   192  51146    Basophils  Blood  Hematology   
2      STAT      None  35420907   619  51200  Eosinophils  Blood  Hematology   
3      STAT      None  35420907   765  51221   Hematocrit  Blood  Hematology   
4      STAT      None  35420907   775  51222   Hemoglobin  Blood  Hematology   
5      STAT      None  35420907   991  51244  Lymphocytes  Blood  Hematology   
6      STAT      None  35420907  1016  51248          MCH  Blood  Hematology   
7      STAT      None  35420907  1017  51249         MCHC  Blood  Hematology   
8      STAT      None  35420907  1019  51250          MCV  Blood  Hematology   
9      STAT      None  35420907  1051  51254    Monocytes  Blood  Hematology   

  loinc_code  
0     2823-3  
1      704-7  
2      711-2  
3     4544-3  
4      718-7  
5      731-0  
6      785-6  
7      786-4  
8      787-2  
9      742-7  

[10 rows x 23 columns]

# Tables disponibles

L'ensemble des tables disponible est le suivant :

In [51]:
pd.read_sql("""
    SELECT tbl_name AS nom_de_la_table
    FROM sqlite_master
    GROUP BY tbl_name
""", conn)

nom_de_la_table
0          d_labitems
1           diagnosis
2             edstays
3           labevents
4            medrecon
5  microbiologyevents
6            patients
7              triage

L'ensemble des tables correspondent aux fichiers correspondant au sein de MIMIC-IV-ED.  
Il y a quelques exceptions qui proviennent de MIMIC-IV :
- labevents
- microbiologyevents
- d_labitems

### d_labitems

d_labitems contient le libellé des examens de biologie.  
Chaque libellé a un identifiant unique `itemid`. Il est utile à l'identification des examens dans la table labevents.

Plus de détail ici : https://mimic.mit.edu/docs/iv/modules/hosp/d_labitems/

In [54]:
pd.read_sql("SELECT * FROM d_labitems LIMIT 10", conn)

index  itemid                      label             fluid    category  \
0      0   51905                             Other Body Fluid   Chemistry   
1      1   51532     11-Deoxycorticosterone             Blood   Chemistry   
2      2   51957  17-Hydroxycorticosteroids             Urine   Chemistry   
3      3   51958     17-Ketosteroids, Urine             Urine   Chemistry   
4      4   52068                      24 Hr             Blood  Hematology   
5      5   51066              24 hr Calcium             Urine   Chemistry   
6      6   51067           24 hr Creatinine             Urine   Chemistry   
7      7   51068              24 hr Protein             Urine   Chemistry   
8      8   50853            25-OH Vitamin D             Blood   Chemistry   
9      9   51533                         3t             Blood   Chemistry   

  loinc_code  
0       None  
1       None  
2       None  
3       None  
4       None  
5       None  
6       None  
7       None  
8       None  
9       None

### labevents

labevents contient les examents de biologie ainsi que leurs résultat.
Chaque examen a deux dates associés :
- charttime qui est la date de réception de l'examen, on peux la considérer comme une approximation de la date de prélèvement
- storetime date de mise à disposition du résultat de l'examen, selon l'examen celle-ci est plus où moins espacé de la date de prélèvement

Chaque ligne correspond au résultat d'un examen (par exemple, dosage du potassium, identifié par `itemid`) et est identifié par un identifiant unique `labevent_id`. Plusieurs examens peuvent être effectué sur le même prélèvement sanguin.  
Chaque prélèvement est identifié par un identifiant unique `specimen_id`.  
Enfin, `subject_id` identifie le patient, `hadm_id` l'identifiant de séjour lorsque le patient a été hospitalisé au décours de son passage aux urgences et `stay_id` l'identifiant du passage aux urgences.

Plus de détail ici : https://mimic.mit.edu/docs/iv/modules/hosp/labevents/

In [60]:
pd.read_sql("SELECT * FROM labevents LIMIT 10", conn)

index  labevent_id  subject_id hadm_id  specimen_id  itemid  \
0      0         2599    10000764    None     76601642   50971   
1      1         2578    10000764    None      6228584   51146   
2      2         2579    10000764    None      6228584   51200   
3      3         2580    10000764    None      6228584   51221   
4      4         2581    10000764    None      6228584   51222   
5      5         2582    10000764    None      6228584   51244   
6      6         2583    10000764    None      6228584   51248   
7      7         2584    10000764    None      6228584   51249   
8      8         2585    10000764    None      6228584   51250   
9      9         2586    10000764    None      6228584   51254   

             charttime            storetime value  valuenum valueuom  \
0  2132-10-14 20:15:00  2132-10-14 21:04:00   4.1       4.1    mEq/L   
1  2132-10-14 20:15:00  2132-10-14 20:33:00   0.1       0.1        %   
2  2132-10-14 20:15:00  2132-10-14 20:33:00   0.3       0.3        %   
3  2132-10-14 20:15:00  2132-10-14 20:33:00  40.2      40.2        %   
4  2132-10-14 20:15:00  2132-10-14 20:33:00  14.1      14.1     g/dL   
5  2132-10-14 20:15:00  2132-10-14 20:33:00   4.7       4.7        %   
6  2132-10-14 20:15:00  2132-10-14 20:33:00  32.8      32.8       pg   
7  2132-10-14 20:15:00  2132-10-14 20:33:00  35.1      35.1        %   
8  2132-10-14 20:15:00  2132-10-14 20:33:00    93      93.0       fL   
9  2132-10-14 20:15:00  2132-10-14 20:33:00   3.8       3.8        %   

   ref_range_lower  ref_range_upper      flag priority comments   stay_id  
0              3.3              5.1      None     STAT     None  35420907  
1              0.0              2.0      None     STAT     None  35420907  
2              0.0              4.0      None     STAT     None  35420907  
3             40.0             52.0      None     STAT     None  35420907  
4             14.0             18.0      None     STAT     None  35420907  
5             18.0             42.0  abnormal     STAT     None  35420907  
6             27.0             32.0  abnormal     STAT     None  35420907  
7             31.0             35.0  abnormal     STAT     None  35420907  
8             82.0             98.0      None     STAT     None  35420907  
9              2.0             11.0      None     STAT     None  35420907

### microbiologyevents

Parmis les examens de biologie, certains revêtent d'un statut particulier, il s'agit des examens de microbiologie, c'est à dire les examens recherchant la présence de bactérie dans un prélèvement biologique (sang, urine, selle, liquide céphalo-rachidien ...).

Ils sont enregistrés dans une table dédié : microbiologyevents  
Le champs "spec_type_desc" contient le site de prélèvement, souvent le sang (BLOOD CULTURE) où les urines (URINES) (cf plus bas).

L'interprétation de ces examens faisant l'objet de spécificté, on retrouve de nombreuses colonnes spécifiant : la valeur quantitative de l'analyse, son interprétation, le nimbre de résistance de la bactérie identifié ... En première intention, il semble qu'il s'agit de champs que nous n'aurons pas à exploiter.

Plus de détail ici : https://mimic.mit.edu/docs/iv/modules/hosp/microbiologyevents/

In [69]:
pd.read_sql("SELECT * FROM microbiologyevents LIMIT 10", conn)

index  microevent_id  subject_id hadm_id  micro_specimen_id  \
0      0           1562    10004235    None             139903   
1      1           1558    10004235    None             139903   
2      2           1559    10004235    None             139903   
3      3           1560    10004235    None             139903   
4      4           1561    10004235    None             139903   
5      5           1563    10004235    None             139903   
6      6           1564    10004235    None             139903   
7      7           1565    10004235    None             139903   
8      8           1566    10004235    None             139903   
9      9           1567    10004235    None             139903   

             chartdate            charttime  spec_itemid spec_type_desc  \
0  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
1  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
2  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
3  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
4  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
5  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
6  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
7  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
8  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   
9  2196-02-24 00:00:00  2196-02-24 12:40:00        70012  BLOOD CULTURE   

   test_seq  ... isolate_num quantity  ab_itemid               ab_name  \
0         1  ...         1.0     None    90013.0            TOBRAMYCIN   
1         1  ...         1.0     None    90004.0            AMPICILLIN   
2         1  ...         1.0     None    90005.0             CEFAZOLIN   
3         1  ...         1.0     None    90008.0    TRIMETHOPRIM/SULFA   
4         1  ...         1.0     None    90012.0            GENTAMICIN   
5         1  ...         1.0     None    90017.0           CEFTAZIDIME   
6         1  ...         1.0     None    90018.0           CEFTRIAXONE   
7         1  ...         1.0     None    90019.0         CIPROFLOXACIN   
8         1  ...         1.0     None    90022.0  AMPICILLIN/SULBACTAM   
9         1  ...         1.0     None    90026.0     PIPERACILLIN/TAZO   

   dilution_text dilution_comparison  dilution_value interpretation  comments  \
0            <=1          <=                    1.00              S      None   
1              8          =                     8.00              S      None   
2            <=4          <=                    4.00              S      None   
3            <=1          <=                    1.00              S      None   
4            <=1          <=                    1.00              S      None   
5            <=1          <=                    1.00              S      None   
6            <=1          <=                    1.00              S      None   
7         <=0.25          <=                    0.25              S      None   
8            <=2          <=                    2.00              S      None   
9            <=4          <=                    4.00              S      None   

    stay_id  
0  38926302  
1  38926302  
2  38926302  
3  38926302  
4  38926302  
5  38926302  
6  38926302  
7  38926302  
8  38926302  
9  38926302  

[10 rows x 26 columns]

In [70]:
pd.read_sql("SELECT spec_type_desc, COUNT(0) total FROM microbiologyevents GROUP BY spec_type_desc", conn).sort_values("total", ascending=False).head(10)

spec_type_desc   total
53             URINE  186509
6      BLOOD CULTURE  177616
47              SWAB   15476
35  PERITONEAL FLUID    5923
45             STOOL    5426
18  CSF;SPINAL FLUID    3847
1            ABSCESS    3011
32       JOINT FLUID    2341
52            TISSUE    1825
44            SPUTUM    1587

### edstays

La table edstays contient la liste de tout les passages aux urgences.  
Sont enregistré : l'identifiant du patient, l'identifiant du séjour si le patient est hospitalisé en aval de son passage aux urgences, l'identifiant du passage aux urgences, la date et heure d'entrée et sortie.

Plus de détail ici : https://mimic.mit.edu/docs/iv/modules/ed/edstays/

In [62]:
pd.read_sql("SELECT * FROM edstays LIMIT 10", conn)

index  subject_id     hadm_id   stay_id               intime  \
0      0    10000115         NaN  38081480  2154-12-10 02:04:00   
1      1    10000115         NaN  30295111  2154-12-17 16:37:00   
2      2    10000473         NaN  33267868  2138-03-15 20:07:00   
3      3    10000764  27897940.0  35420907  2132-10-14 19:31:00   
4      4    10001038         NaN  34301067  2149-08-07 08:51:00   
5      5    10001757         NaN  30596003  2170-10-15 11:06:00   
6      6    10002563         NaN  36308013  2192-11-08 14:00:00   
7      7    10003299  28891311.0  33780565  2178-12-10 17:04:00   
8      8    10003299  21404960.0  39680380  2179-06-30 09:18:00   
9      9    10003299  29323205.0  32908139  2181-10-22 11:46:00   

               outtime  
0  2154-12-10 02:16:00  
1  2154-12-17 17:38:00  
2  2138-03-15 20:26:00  
3  2132-10-14 23:32:59  
4  2149-08-07 08:55:00  
5  2170-10-15 11:26:00  
6  2192-11-08 14:23:00  
7  2178-12-10 21:36:00  
8  2179-06-30 16:35:45  
9  2181-10-22 19:09:15

### patients

La table patient contient la liste des patients ainsi que les information relative à leurs age et genre.  
La base MIMIC-IV étant pseudonymisé, toutes les dates ont été falsifié, la table patient nous donne une approximation de la véritable date des enregistrement dans le champs anchor_year_group.

Plus d'informations ici : https://mimic.mit.edu/docs/iv/modules/core/patients/

In [74]:
pd.read_sql("SELECT * FROM patients LIMIT 10", conn)

index  subject_id gender  anchor_age  anchor_year anchor_year_group   dod
0      0    10021917      M          54         2147       2017 - 2019  None
1      1    10033879      F          28         2173       2011 - 2013  None
2      2    10036909      M          50         2167       2011 - 2013  None
3      3    10050355      F          55         2168       2014 - 2016  None
4      4    10050389      M          43         2133       2014 - 2016  None
5      5    10050411      F          52         2150       2017 - 2019  None
6      6    10068290      M          29         2151       2014 - 2016  None
7      7    10127166      F          51         2149       2008 - 2010  None
8      8    10143090      M          48         2155       2011 - 2013  None
9      9    10148710      M          67         2137       2008 - 2010  None

### triage

La table triage contient les données de "tri" des patients.  
Le circuit classique d'un passage aux urgences est le suivant :
- Enregistrement administratif du patient
- Patient reçu rapidement par un infirmier (en France on parle d'infirmier d'accueil et d'orientation, où IAO)
- Un niveau de sévèrité est attribué au patient par l'IAO
- Le médecin voit ensuite le patient, dès qu'il le peut, par ordre de priorité et d'attente
- Si le médecin a besoin de plus d'éléments, il prescrit des examens complémentaires au patient

Ainsi, l'ensemble des informations disponible à l'arrivé du patient sont enregistré dans cette table.

Le champs chiefcomplaint est un champs de texte libre, le reste contient des variables quantitative de paramètre vitaux recueillis par l'IAO.  
Ce champs peux contenir une liste, qui est alors séparé par une virgule.  
Il s'agit d'un champs qui a fait l'objet d'une désidentification, ainsi si une information personnelle était présente dans la liste, elle est remplacé par le caractère "___" (3 underscore à la suite).


In [77]:
pd.read_sql("SELECT * FROM triage LIMIT 10", conn)

index  subject_id   stay_id  temperature  heartrate  resprate  o2sat  \
0      0    15585360  37573921         97.0       87.0      18.0  100.0   
1      1    17192424  34160628         98.6       82.0       NaN  100.0   
2      2    15248757  32172727         97.1      112.0      20.0  100.0   
3      3    16648037  38946064         98.5       59.0      18.0   99.0   
4      4    13492931  39828574        100.6       90.0      16.0   96.0   
5      5    11475777  38193311         97.1       85.0      16.0  100.0   
6      6    16615356  38143467         98.5      100.0      16.0  100.0   
7      7    17748455  33063682         99.4      152.0      18.0   96.0   
8      8    13718556  30494050         98.5       84.0      14.0  100.0   
9      9    13908077  39580901         97.0       96.0      18.0   98.0   

     sbp   dbp  pain  acuity chiefcomplaint  
0  150.0  71.0  10.0     3.0              
1  111.0  81.0   3.0     3.0                
2  147.0  97.0   8.0     4.0               
3  160.0  86.0   2.0     2.0                
4  107.0  55.0   0.0     3.0              '  
5  138.0  86.0   7.0     3.0              -  
6  130.0  94.0   8.0     3.0              -  
7  136.0  77.0   0.0     1.0              -  
8  124.0  92.0   4.0     3.0              -  
9  129.0  44.0   4.0     2.0              -

In [93]:
pd.read_sql("SELECT * FROM triage WHERE LENGTH(chiefcomplaint) > 50 LIMIT 10", conn)

index  subject_id   stay_id  temperature  heartrate  resprate  o2sat  \
0   1305    12601251  34627547         98.3       81.0      16.0  100.0   
1   1308    16663465  36113926         98.8       58.0      18.0   98.0   
2   1331    14248362  34323484         98.3       90.0      17.0   98.0   
3   1332    11493670  35944304         96.4       80.0      17.0   99.0   
4   1340    15032149  34358091         96.6       51.0      20.0  100.0   
5   1341    18160217  37565547         98.1       82.0      16.0  100.0   
6   1345    14539683  30348440         96.9       80.0      14.0  100.0   
7   1346    12491283  39692564         97.7       88.0      18.0   99.0   
8   1350    16220647  39977711         98.3       94.0      16.0  100.0   
9   1368    14912902  36669324         98.4      119.0      18.0   96.0   

     sbp   dbp  pain  acuity  \
0  172.0  65.0   3.0     3.0   
1  176.0  71.0   7.0     2.0   
2  140.0  70.0   0.0     2.0   
3  105.0  65.0   0.0     2.0   
4  128.0  77.0   2.0     2.0   
5  116.0  55.0   0.0     3.0   
6  128.0  58.0   NaN     2.0   
7  116.0  70.0   7.0     2.0   
8  121.0  63.0   6.0     3.0   
9  124.0  76.0   7.0     2.0   

                                      chiefcomplaint  
0  Abdominal distention, Abd pain, Dyspnea on exe...  
1  Abdominal distention, Abd pain, S/P KIDNEY TRA...  
2  Abdominal distention, Abnormal labs, Jaundice,...  
3  Abdominal distention, Abnormal labs, Jaundice,...  
4  Abdominal distention, Abnormal sodium level, A...  
5  Abdominal distention, Abnormal sodium level, T...  
6  Abdominal distention, Altered mental status, J...  
7  Abdominal distention, Altered mental status, J...  
8  Abdominal distention, Anemia, Dyspnea, RUQ abd...  
9  Abdominal distention, Back pain, L Shoulder pa...

### medrecon

La table medrecon contient la liste des traitements habituels du patient.  
Par traitement habituel, on entends les traitement que le patient prenait avant même son passage aux urgences.

Ces traitements sont tous identifiés à l'aide d'identifiant produit :
- NDC - National Drug Classification (de la NDA)
- GSN - Generic sequence number

Les traitements ont été regroupés à l'aide d'une classification nommé "Enhanced Therapeutic Class", chaque groupe est identifié par un code `etccode` associé au libelé du groupe `etcdescription`.

Une analyse plus poussée des traitements pourrait être nécessaires, elle imposerait d'exploiter le code produit NDC.  
L'idéal est d'obtenir un code ATC, qui est une classification fonctionnelle très pratique pour identifier l'indication des médicaments.  
Une approche pourrait être de se reposer sur l'API de la `National Library of Medicine` (https://lhncbc.nlm.nih.gov/RxNav/).  
Une travail similaire a été effectué par d'autres personnes : https://github.com/fabkury/ndc_map

In [97]:
pd.read_sql("SELECT * FROM medrecon LIMIT 10", conn)

index  subject_id   stay_id            charttime                    name  \
0      0    12363835  34078373  2177-02-13 03:31:00        Caltrate 600 + D   
1      1    12363835  34078373  2177-02-13 03:31:00                Coumadin   
2      2    12363835  34078373  2177-02-13 03:31:00                 Flonase   
3      3    12363835  34078373  2177-02-13 03:31:00               lidocaine   
4      4    12363835  34078373  2177-02-13 03:31:00              omeprazole   
5      5    12363835  34078373  2177-02-13 03:31:00          ranitidine HCl   
6      6    12363835  34078373  2177-02-13 03:31:00  Tylenol Extra Strength   
7      7    15128994  30058281  2167-08-29 04:27:00               Dialyvite   
8      8    15128994  30058281  2167-08-29 04:27:00             allopurinol   
9      9    15128994  30058281  2167-08-29 04:27:00       albuterol sulfate   

     gsn          ndc  etc_rn  etccode  \
0  63395  11845014031       1   6143.0   
1   6562  15330026801       1    806.0   
2  18368  12280027016       1    301.0   
3  43256  10544037630       1   3932.0   
4  43137  16714074801       1    445.0   
5  11674  10544036030       1    443.0   
6   4490  10003011501       1    577.0   
7  60020  10542000010       1    690.0   
8   2535  11289101302       1   2602.0   
9  28090  21695042308       1   5970.0   

                                      etcdescription  
0  Minerals and Electrolytes - Calcium Replacemen...  
1                          Anticoagulants - Coumarin  
2                              Nasal Corticosteroids  
3   Dermatological - Topical Local Anesthetic Amides  
4  Gastric Acid Secretion Reducing Agents - Proto...  
5  Gastric Acid Secretion Reducers - Histamine H2...  
6                Analgesic or Antipyretic Non-Opioid  
7                     B-Complex Vitamin Combinations  
8  Hyperuricemia Therapy - Xanthine Oxidase Inhib...  
9  Asthma/COPD Therapy - Beta 2-Adrenergic Agents...

### diagnosis

Bien que ne faisant pas partit de l'objet du projet, la table `diagnosis` a été inclut dans l'éventualité où nous aurions besoin de l'explorer.  
L'ensemble des diagnostic sont identifié à l'aide de la classification internationale des maladie dans sa version 9 (ICD-9).

In [98]:
pd.read_sql("SELECT * FROM diagnosis LIMIT 10", conn)

index  subject_id   stay_id  seq_num icd_code  icd_version  \
0      0    15825222  39090953        1      486            9   
1      1    15825222  39090953        2     4254            9   
2      2    11554870  37245764        1     5609            9   
3      3    19748558  30511202        1    49392            9   
4      4    18008347  34907903        1     7842            9   
5      5    15475846  30308014        1    78079            9   
6      6    15475846  30308014        2    27651            9   
7      7    16538197  33556881        1     6084            9   
8      8    18438529  35200231        1    30500            9   
9      9    17185991  37532781        1     7840            9   

                                      icd_title  
0                PNEUMONIA,ORGANISM UNSPECIFIED  
1                       PRIM CARDIOMYOPATHY NEC  
2                       INTESTINAL OBSTRUCT NOS  
3  ASTHMA, UNSPECIFIED, WITH ACUTE EXACERBATION  
4                       SWELLING IN HEAD & NECK  
5                     OTHER MALAISE AND FATIGUE  
6                                   DEHYDRATION  
7                       MALE GEN INFLAM DIS NEC  
8                          ALCOHOL ABUSE-UNSPEC  
9                                      HEADACHE